# Load data

In [1]:
import pandas as pd
from sklearn.model_selection import cross_validate

In [2]:
test = pd.read_csv('test.csv')
test.head()

id cat0 cat1 cat2 cat3 cat4 cat5 cat6 cat7 cat8  ...     cont4     cont5  \
0   0    A    B    A    C    B    D    A    E    E  ...  0.701679  0.595507   
1   5    A    B    A    C    B    D    A    E    C  ...  0.277480  0.479552   
2  15    A    B    A    C    B    D    A    E    C  ...  0.279508  0.676395   
3  16    A    A    B    A    B    D    A    E    E  ...  0.479503  0.759875   
4  17    A    B    A    A    B    B    A    E    E  ...  0.757845  0.210232   

      cont6     cont7     cont8     cont9    cont10    cont11    cont12  \
0  0.286912  0.279884  0.202234  0.242654  0.285147  0.264308  0.653654   
1  0.397436  0.476742  0.857073  0.516393  0.562065  0.730542  0.318492   
2  0.695284  0.253316  0.586934  0.548555  0.836193  0.759788  0.333572   
3  0.240049  0.298074  0.442475  0.596746  0.414131  0.255382  0.589080   
4  0.329851  0.616663  0.170475  0.263235  0.710961  0.224045  0.285860   

     cont13  
0  0.302448  
1  0.736251  
2  0.273905  
3  0.311625  
4  0.794931  

[5 rows x 25 columns]

In [3]:
train = pd.read_csv('train.csv')
train.head()
train = train.sample(frac=1, random_state=42)
train.head()

id cat0 cat1 cat2 cat3 cat4 cat5 cat6 cat7 cat8  ...     cont5  \
4941      8330    B    A    A    A    B    B    A    E    E  ...  0.377936   
51775    86091    A    A    A    A    B    D    A    E    E  ...  0.398920   
115253  192120    A    A    B    A    B    D    A    E    G  ...  0.835372   
299321  498914    A    A    A    C    B    B    A    E    E  ...  0.745390   
173570  289384    A    A    A    C    B    B    A    E    D  ...  0.227085   

           cont6     cont7     cont8     cont9    cont10    cont11    cont12  \
4941    0.695889  0.225072  0.279877  0.397533  0.346235  0.318158  0.322053   
51775   0.541013  0.261724  0.300421  0.210114  0.356237  0.298105  0.294468   
115253  0.328593  0.777681  0.266530  0.654293  0.464221  0.698295  0.831430   
299321  0.384305  0.251359  0.249770  0.334739  0.386494  0.358721  0.305164   
173570  0.367200  0.271663  0.302262  0.316547  0.528495  0.290432  0.331302   

          cont13    target  
4941    0.731761  5.733432  
51775   0.757850  6.990234  
115253  0.798729  8.212900  
299321  0.756006  8.466549  
173570  0.308376  7.449541  

[5 rows x 26 columns]

In [4]:
cat_cols = [x for x in train.columns if x.startswith('cat')]
cat_cols

['cat0',
 'cat1',
 'cat2',
 'cat3',
 'cat4',
 'cat5',
 'cat6',
 'cat7',
 'cat8',
 'cat9']

In [5]:
x_train = train.drop(columns=['target','id'])
y_train = train['target']

In [6]:
for cat in cat_cols:
    x_train[cat] = x_train[cat].astype("category")
    test[cat] = test[cat].astype("category")

# Submit

In [7]:
def submit(model, refit = True):
    if refit:
        model.fit(x_train, y_train)
    pred = model.predict(test.drop(columns='id'))
    submission = pd.DataFrame({'id':test['id'], 'target':pred})
    return submission

# Flaml

In [8]:
from flaml import AutoML
automl = AutoML()
automl.fit(x_train, y_train, task="regression", estimator_list=["lgbm"], 
           time_budget=3000, metric='mse', eval_method='cv', n_splits = 5, n_jobs=6)

[flaml.automl: 02-27 14:26:07] {853} INFO - Evaluation method: cv
[flaml.automl: 02-27 14:26:07] {577} INFO - Using RepeatedKFold
[flaml.automl: 02-27 14:26:07] {874} INFO - Minimizing error metric: mse
[flaml.automl: 02-27 14:26:07] {893} INFO - List of ML learners in AutoML Run: ['lgbm']
[flaml.automl: 02-27 14:26:07] {953} INFO - iteration 0  current learner lgbm
[flaml.automl: 02-27 14:26:10] {1101} INFO -  at 4.3s,	best lgbm's error=0.7764,	best lgbm's error=0.7764
[flaml.automl: 02-27 14:26:10] {953} INFO - iteration 1  current learner lgbm
[flaml.automl: 02-27 14:26:12] {1101} INFO -  at 6.5s,	best lgbm's error=0.7764,	best lgbm's error=0.7764
[flaml.automl: 02-27 14:26:12] {953} INFO - iteration 2  current learner lgbm
[flaml.automl: 02-27 14:26:15] {1101} INFO -  at 9.5s,	best lgbm's error=0.7583,	best lgbm's error=0.7583
[flaml.automl: 02-27 14:26:15] {953} INFO - iteration 3  current learner lgbm
[flaml.automl: 02-27 14:26:17] {1101} INFO -  at 11.7s,	best lgbm's error=0.758

[flaml.automl: 02-27 14:47:44] {953} INFO - iteration 43  current learner lgbm
[flaml.automl: 02-27 14:48:21] {1101} INFO -  at 1335.2s,	best lgbm's error=0.7113,	best lgbm's error=0.7113
[flaml.automl: 02-27 14:48:21] {953} INFO - iteration 44  current learner lgbm
[flaml.automl: 02-27 14:50:24] {1101} INFO -  at 1458.0s,	best lgbm's error=0.7113,	best lgbm's error=0.7113
[flaml.automl: 02-27 14:50:24] {953} INFO - iteration 45  current learner lgbm
[flaml.automl: 02-27 14:51:28] {1101} INFO -  at 1522.0s,	best lgbm's error=0.7113,	best lgbm's error=0.7113
[flaml.automl: 02-27 14:51:28] {953} INFO - iteration 46  current learner lgbm
[flaml.automl: 02-27 14:52:04] {1101} INFO -  at 1558.1s,	best lgbm's error=0.7113,	best lgbm's error=0.7113
[flaml.automl: 02-27 14:52:04] {953} INFO - iteration 47  current learner lgbm
[flaml.automl: 02-27 14:52:42] {1101} INFO -  at 1596.0s,	best lgbm's error=0.7113,	best lgbm's error=0.7113
[flaml.automl: 02-27 14:52:42] {953} INFO - iteration 48  cu

In [9]:
automl.model

LGBMRegressor(colsample_bytree=0.9558337807931836,
              learning_rate=0.08159780383630486, max_bin=255,
              min_child_weight=9.183040293854946, n_estimators=2745, n_jobs=6,
              num_leaves=4, objective='regression',
              reg_alpha=1.118956986216362e-08, reg_lambda=0.30555324963577096,
              subsample=0.9886028744100488)

In [10]:
import math
math.sqrt(automl.best_loss)

0.8433784743728898

In [11]:
submission = submit(automl.model, refit = False)
submission.head()

id    target
0   0  7.666896
1   5  7.762883
2  15  7.571860
3  16  7.426724
4  17  7.204717

In [12]:
submission.to_csv('submission_lightgbm_flaml.csv', index=False)

# Lightgbm Optuna

In [13]:
import lightgbm
data = lightgbm.Dataset(x_train, label=y_train)

In [25]:
import optuna.integration.lightgbm as lgb
from sklearn.model_selection import KFold
params = {
        "objective": "regression",
        "metric": "mse",
        "verbosity": 0,
        "boosting_type": "gbdt",
    }

tuner = lgb.LightGBMTunerCV(
    params, data, time_budget=9000, folds=KFold(n_splits=5)
)

tuner.run()

[I 2021-02-27 18:05:04,238] A new study created in memory with name: no-name-80b56bcb-d33d-4328-8d1e-97ad46fe2d36
feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.015204 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006483 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.015006 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014956 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.017686 seconds.
You can set `force_col_wise=true` to remove the overhead.
[1]	cv_agg's l2: 0.780744 + 0.00172999
[2]	cv_agg's l2: 0.775304 + 0.0016637
[3]	cv_agg's l2: 0.770691 + 0.0016

[187]	cv_agg's l2: 0.714234 + 0.00191692
[188]	cv_agg's l2: 0.714239 + 0.0019131
[189]	cv_agg's l2: 0.71424 + 0.0019083
[190]	cv_agg's l2: 0.714246 + 0.00190119
[191]	cv_agg's l2: 0.714243 + 0.00190044
[192]	cv_agg's l2: 0.714247 + 0.0018959
[193]	cv_agg's l2: 0.714245 + 0.00189442
[194]	cv_agg's l2: 0.714248 + 0.001895
[195]	cv_agg's l2: 0.71425 + 0.0018999
[196]	cv_agg's l2: 0.714254 + 0.00190929
[197]	cv_agg's l2: 0.714242 + 0.00190479
[198]	cv_agg's l2: 0.714238 + 0.00189947
[199]	cv_agg's l2: 0.714225 + 0.00190251
[200]	cv_agg's l2: 0.714206 + 0.00191484
[201]	cv_agg's l2: 0.714196 + 0.00192283
[202]	cv_agg's l2: 0.714187 + 0.0019259
[203]	cv_agg's l2: 0.714176 + 0.00192072
[204]	cv_agg's l2: 0.714168 + 0.00192664
[205]	cv_agg's l2: 0.71419 + 0.00192761
[206]	cv_agg's l2: 0.714166 + 0.00195059
[207]	cv_agg's l2: 0.714152 + 0.00194158
[208]	cv_agg's l2: 0.714168 + 0.00193756
[209]	cv_agg's l2: 0.714165 + 0.00192837
[210]	cv_agg's l2: 0.714154 + 0.0019122
[211]	cv_agg's l2: 0.714159

[393]	cv_agg's l2: 0.714493 + 0.00202715
[394]	cv_agg's l2: 0.714502 + 0.00202539
[395]	cv_agg's l2: 0.714499 + 0.00202596
[396]	cv_agg's l2: 0.714489 + 0.00202053
[397]	cv_agg's l2: 0.71449 + 0.00201433
[398]	cv_agg's l2: 0.71448 + 0.00202459
[399]	cv_agg's l2: 0.71448 + 0.00202132
[400]	cv_agg's l2: 0.714482 + 0.00202503
[401]	cv_agg's l2: 0.714495 + 0.00201315
[402]	cv_agg's l2: 0.714505 + 0.00201918
[403]	cv_agg's l2: 0.714503 + 0.00200808
[404]	cv_agg's l2: 0.714516 + 0.0019968
[405]	cv_agg's l2: 0.714533 + 0.00198705
[406]	cv_agg's l2: 0.714539 + 0.00199574
[407]	cv_agg's l2: 0.714544 + 0.00200168
[408]	cv_agg's l2: 0.714555 + 0.0019872
[409]	cv_agg's l2: 0.714565 + 0.00198769
[410]	cv_agg's l2: 0.714559 + 0.00200656
[411]	cv_agg's l2: 0.714562 + 0.00199966
[412]	cv_agg's l2: 0.714584 + 0.00199531
[413]	cv_agg's l2: 0.714602 + 0.00200127
[414]	cv_agg's l2: 0.714605 + 0.00199723
[415]	cv_agg's l2: 0.714611 + 0.00198248
[416]	cv_agg's l2: 0.714619 + 0.00198826
[417]	cv_agg's l2: 0.

[596]	cv_agg's l2: 0.715656 + 0.00216181
[597]	cv_agg's l2: 0.715678 + 0.00215046
[598]	cv_agg's l2: 0.715683 + 0.00215496
[599]	cv_agg's l2: 0.715681 + 0.00214583
[600]	cv_agg's l2: 0.715671 + 0.00213678
[601]	cv_agg's l2: 0.715676 + 0.00213804
[602]	cv_agg's l2: 0.715685 + 0.00213756
[603]	cv_agg's l2: 0.715695 + 0.00213872
[604]	cv_agg's l2: 0.715707 + 0.00211738
[605]	cv_agg's l2: 0.715719 + 0.00210073
[606]	cv_agg's l2: 0.715715 + 0.0021029
[607]	cv_agg's l2: 0.715716 + 0.00211395
[608]	cv_agg's l2: 0.715716 + 0.00213445
[609]	cv_agg's l2: 0.715726 + 0.00212691
[610]	cv_agg's l2: 0.715724 + 0.00211292
[611]	cv_agg's l2: 0.715752 + 0.00212092
[612]	cv_agg's l2: 0.715767 + 0.00212526
[613]	cv_agg's l2: 0.715783 + 0.00213446
[614]	cv_agg's l2: 0.715772 + 0.00214808
[615]	cv_agg's l2: 0.715773 + 0.00213795
[616]	cv_agg's l2: 0.715778 + 0.00212556
[617]	cv_agg's l2: 0.715783 + 0.00213543
[618]	cv_agg's l2: 0.715781 + 0.0021285
[619]	cv_agg's l2: 0.715791 + 0.00213621
[620]	cv_agg's l2:

...

[389]	cv_agg's l2: 0.712183 + 0.00172433
[390]	cv_agg's l2: 0.712175 + 0.00173092
[391]	cv_agg's l2: 0.712166 + 0.00173621
[392]	cv_agg's l2: 0.712162 + 0.00173692
[393]	cv_agg's l2: 0.71216 + 0.00173607
[394]	cv_agg's l2: 0.712149 + 0.00173876
[395]	cv_agg's l2: 0.712134 + 0.00174509
[396]	cv_agg's l2: 0.71212 + 0.00174167
[397]	cv_agg's l2: 0.712115 + 0.0017393
[398]	cv_agg's l2: 0.712099 + 0.00175456
[399]	cv_agg's l2: 0.712097 + 0.00175461
[400]	cv_agg's l2: 0.712092 + 0.00175534
[401]	cv_agg's l2: 0.712096 + 0.00175165
[402]	cv_agg's l2: 0.712092 + 0.00174766
[403]	cv_agg's l2: 0.712078 + 0.00175104
[404]	cv_agg's l2: 0.71207 + 0.0017513
[405]	cv_agg's l2: 0.712055 + 0.0017526
[406]	cv_agg's l2: 0.71206 + 0.00175524
[407]	cv_agg's l2: 0.71204 + 0.00175074
[408]	cv_agg's l2: 0.712044 + 0.00175456
[409]	cv_agg's l2: 0.71203 + 0.00174911
[410]	cv_agg's l2: 0.712028 + 0.00174441
[411]	cv_agg's l2: 0.712027 + 0.00174492
[412]	cv_agg's l2: 0.712019 + 0.0017427
[413]	cv_agg's l2: 0.71201

[599]	cv_agg's l2: 0.711382 + 0.00181268
[600]	cv_agg's l2: 0.711381 + 0.00180798
[601]	cv_agg's l2: 0.711377 + 0.00180371
[602]	cv_agg's l2: 0.711375 + 0.0018064
[603]	cv_agg's l2: 0.711373 + 0.00180864
[604]	cv_agg's l2: 0.711375 + 0.00180464
[605]	cv_agg's l2: 0.711374 + 0.00180606
[606]	cv_agg's l2: 0.711375 + 0.00180835
[607]	cv_agg's l2: 0.711372 + 0.00181181
[608]	cv_agg's l2: 0.711377 + 0.00180999
[609]	cv_agg's l2: 0.711377 + 0.00180916
[610]	cv_agg's l2: 0.711374 + 0.00181129
[611]	cv_agg's l2: 0.711364 + 0.00181235
[612]	cv_agg's l2: 0.711363 + 0.00181071
[613]	cv_agg's l2: 0.711358 + 0.0018126
[614]	cv_agg's l2: 0.711361 + 0.00180492
[615]	cv_agg's l2: 0.711356 + 0.00180031
[616]	cv_agg's l2: 0.711352 + 0.00179821
[617]	cv_agg's l2: 0.711352 + 0.00179828
[618]	cv_agg's l2: 0.711351 + 0.00180433
[619]	cv_agg's l2: 0.711347 + 0.00179642
[620]	cv_agg's l2: 0.71135 + 0.00179749
[621]	cv_agg's l2: 0.711344 + 0.00179941
[622]	cv_agg's l2: 0.711342 + 0.00180281
[623]	cv_agg's l2: 

[807]	cv_agg's l2: 0.711093 + 0.00181239
[808]	cv_agg's l2: 0.711088 + 0.00181642
[809]	cv_agg's l2: 0.711095 + 0.00181923
[810]	cv_agg's l2: 0.71109 + 0.00181918
[811]	cv_agg's l2: 0.711086 + 0.00181402
[812]	cv_agg's l2: 0.711089 + 0.00181083
[813]	cv_agg's l2: 0.711086 + 0.00180953
[814]	cv_agg's l2: 0.71108 + 0.00180781
[815]	cv_agg's l2: 0.711079 + 0.00180731
[816]	cv_agg's l2: 0.711083 + 0.00180311
[817]	cv_agg's l2: 0.711084 + 0.00180562
[818]	cv_agg's l2: 0.711081 + 0.00180448
[819]	cv_agg's l2: 0.711074 + 0.00180709
[820]	cv_agg's l2: 0.711067 + 0.00180827
[821]	cv_agg's l2: 0.711073 + 0.00180691
[822]	cv_agg's l2: 0.711076 + 0.00180882
[823]	cv_agg's l2: 0.711075 + 0.0018075
[824]	cv_agg's l2: 0.711079 + 0.00180937
[825]	cv_agg's l2: 0.711078 + 0.00180891
[826]	cv_agg's l2: 0.711075 + 0.00181448
[827]	cv_agg's l2: 0.711072 + 0.00181782
[828]	cv_agg's l2: 0.71107 + 0.00181555
[829]	cv_agg's l2: 0.711069 + 0.00181205
[830]	cv_agg's l2: 0.711065 + 0.00181395
[831]	cv_agg's l2: 0

min_data_in_leaf, val_score: 0.711010: 100%|##########| 5/5 [02:00<00:00, 24.00s/it]

[997]	cv_agg's l2: 0.711115 + 0.00180988
[998]	cv_agg's l2: 0.711114 + 0.0018076
[999]	cv_agg's l2: 0.711113 + 0.00181043
[1000]	cv_agg's l2: 0.711108 + 0.00181056


In [26]:
import math
math.sqrt(tuner.best_score)

0.8432141139969206

In [29]:
tuner.best_params

{'objective': 'regression',
 'metric': 'l2',
 'verbosity': 0,
 'boosting_type': 'gbdt',
 'feature_pre_filter': False,
 'lambda_l1': 9.850984337834847,
 'lambda_l2': 2.9201621366722273e-05,
 'num_leaves': 10,
 'feature_fraction': 0.4,
 'bagging_fraction': 0.9438882305097485,
 'bagging_freq': 1,
 'min_child_samples': 50}

# Train a lightgbm boosted tree (default parameters)

In [13]:
from lightgbm.sklearn import LGBMRegressor

In [14]:
bt = LGBMRegressor(n_jobs=-2)

In [15]:
scores = cross_validate(bt, X=x_train, y=y_train, cv=5, return_train_score = True,
                         scoring='neg_root_mean_squared_error')

In [16]:
scores

{'fit_time': array([1.22706318, 1.18083525, 1.15409446, 1.17929196, 1.16860175]),
 'score_time': array([0.08760285, 0.09076786, 0.09165931, 0.09075093, 0.0900774 ]),
 'test_score': array([-0.84593716, -0.84811234, -0.84677842, -0.84532452, -0.84509775]),
 'train_score': array([-0.83678672, -0.83618969, -0.83649384, -0.83679032, -0.83688036])}

In [17]:
scores['test_score'].mean()

-0.8462500379112754

In [18]:
submission = submit(bt)
submission.head()

id    target
0   0  7.621181
1   5  7.865160
2  15  7.602939
3  16  7.441470
4  17  7.256050

In [14]:
submission.to_csv('submission_lightgbm_default.csv', index=False)

# Train a catboost model (default parameters)

In [8]:
from catboost import CatBoostRegressor

In [9]:
cbr = CatBoostRegressor(cat_features=cat_cols, thread_count=6)

In [10]:
scores = cross_validate(cbr, X=x_train, y=y_train, cv=5, return_train_score = True,                        
                         scoring='neg_root_mean_squared_error')

Learning rate set to 0.103533
0:	learn: 0.8837729	total: 191ms	remaining: 3m 10s
1:	learn: 0.8811223	total: 269ms	remaining: 2m 14s
2:	learn: 0.8788712	total: 383ms	remaining: 2m 7s
3:	learn: 0.8769321	total: 452ms	remaining: 1m 52s
4:	learn: 0.8753202	total: 534ms	remaining: 1m 46s
5:	learn: 0.8736118	total: 649ms	remaining: 1m 47s
6:	learn: 0.8722263	total: 736ms	remaining: 1m 44s
7:	learn: 0.8710068	total: 824ms	remaining: 1m 42s
8:	learn: 0.8697825	total: 918ms	remaining: 1m 41s
9:	learn: 0.8687360	total: 1.01s	remaining: 1m 39s
10:	learn: 0.8677390	total: 1.09s	remaining: 1m 37s
11:	learn: 0.8669163	total: 1.19s	remaining: 1m 37s
12:	learn: 0.8661553	total: 1.27s	remaining: 1m 36s
13:	learn: 0.8653393	total: 1.36s	remaining: 1m 36s
14:	learn: 0.8645831	total: 1.45s	remaining: 1m 35s
15:	learn: 0.8639242	total: 1.53s	remaining: 1m 34s
16:	learn: 0.8633693	total: 1.6s	remaining: 1m 32s
17:	learn: 0.8628391	total: 1.68s	remaining: 1m 31s
18:	learn: 0.8622867	total: 1.79s	remaining: 1

157:	learn: 0.8444963	total: 15.8s	remaining: 1m 24s
158:	learn: 0.8444437	total: 15.9s	remaining: 1m 24s
159:	learn: 0.8443628	total: 16s	remaining: 1m 24s
160:	learn: 0.8442982	total: 16.1s	remaining: 1m 24s
161:	learn: 0.8442421	total: 16.2s	remaining: 1m 24s
162:	learn: 0.8441735	total: 16.4s	remaining: 1m 23s
163:	learn: 0.8441079	total: 16.5s	remaining: 1m 23s
164:	learn: 0.8440362	total: 16.6s	remaining: 1m 23s
165:	learn: 0.8439763	total: 16.7s	remaining: 1m 23s
166:	learn: 0.8439109	total: 16.8s	remaining: 1m 23s
167:	learn: 0.8438452	total: 16.9s	remaining: 1m 23s
168:	learn: 0.8437931	total: 17s	remaining: 1m 23s
169:	learn: 0.8437318	total: 17.1s	remaining: 1m 23s
170:	learn: 0.8436771	total: 17.2s	remaining: 1m 23s
171:	learn: 0.8436161	total: 17.3s	remaining: 1m 23s
172:	learn: 0.8435546	total: 17.4s	remaining: 1m 23s
173:	learn: 0.8435003	total: 17.5s	remaining: 1m 23s
174:	learn: 0.8434542	total: 17.6s	remaining: 1m 22s
175:	learn: 0.8433718	total: 17.7s	remaining: 1m 2

313:	learn: 0.8380491	total: 31.8s	remaining: 1m 9s
314:	learn: 0.8380365	total: 31.9s	remaining: 1m 9s
315:	learn: 0.8379803	total: 32s	remaining: 1m 9s
316:	learn: 0.8379555	total: 32.1s	remaining: 1m 9s
317:	learn: 0.8379276	total: 32.2s	remaining: 1m 9s
318:	learn: 0.8378890	total: 32.3s	remaining: 1m 8s
319:	learn: 0.8378573	total: 32.4s	remaining: 1m 8s
320:	learn: 0.8378377	total: 32.5s	remaining: 1m 8s
321:	learn: 0.8378323	total: 32.6s	remaining: 1m 8s
322:	learn: 0.8377819	total: 32.7s	remaining: 1m 8s
323:	learn: 0.8377472	total: 32.8s	remaining: 1m 8s
324:	learn: 0.8377104	total: 32.9s	remaining: 1m 8s
325:	learn: 0.8376846	total: 33s	remaining: 1m 8s
326:	learn: 0.8376537	total: 33.1s	remaining: 1m 8s
327:	learn: 0.8376155	total: 33.2s	remaining: 1m 8s
328:	learn: 0.8375806	total: 33.3s	remaining: 1m 7s
329:	learn: 0.8375723	total: 33.4s	remaining: 1m 7s
330:	learn: 0.8375310	total: 33.5s	remaining: 1m 7s
331:	learn: 0.8374991	total: 33.6s	remaining: 1m 7s
332:	learn: 0.83

474:	learn: 0.8332626	total: 48.2s	remaining: 53.3s
475:	learn: 0.8332248	total: 48.3s	remaining: 53.1s
476:	learn: 0.8332047	total: 48.4s	remaining: 53.1s
477:	learn: 0.8331711	total: 48.5s	remaining: 53s
478:	learn: 0.8331438	total: 48.6s	remaining: 52.8s
479:	learn: 0.8331111	total: 48.7s	remaining: 52.7s
480:	learn: 0.8330923	total: 48.8s	remaining: 52.6s
481:	learn: 0.8330521	total: 48.9s	remaining: 52.5s
482:	learn: 0.8330100	total: 49s	remaining: 52.4s
483:	learn: 0.8329956	total: 49.1s	remaining: 52.3s
484:	learn: 0.8329653	total: 49.2s	remaining: 52.2s
485:	learn: 0.8329476	total: 49.3s	remaining: 52.1s
486:	learn: 0.8329294	total: 49.4s	remaining: 52s
487:	learn: 0.8329200	total: 49.5s	remaining: 51.9s
488:	learn: 0.8328845	total: 49.6s	remaining: 51.8s
489:	learn: 0.8328507	total: 49.7s	remaining: 51.7s
490:	learn: 0.8328335	total: 49.8s	remaining: 51.6s
491:	learn: 0.8328108	total: 49.9s	remaining: 51.5s
492:	learn: 0.8327781	total: 50s	remaining: 51.5s
493:	learn: 0.832750

636:	learn: 0.8293971	total: 1m 4s	remaining: 36.6s
637:	learn: 0.8293688	total: 1m 4s	remaining: 36.5s
638:	learn: 0.8293518	total: 1m 4s	remaining: 36.4s
639:	learn: 0.8293282	total: 1m 4s	remaining: 36.3s
640:	learn: 0.8293025	total: 1m 4s	remaining: 36.3s
641:	learn: 0.8292644	total: 1m 4s	remaining: 36.2s
642:	learn: 0.8292266	total: 1m 4s	remaining: 36.1s
643:	learn: 0.8292024	total: 1m 5s	remaining: 36s
644:	learn: 0.8291926	total: 1m 5s	remaining: 35.9s
645:	learn: 0.8291812	total: 1m 5s	remaining: 35.8s
646:	learn: 0.8291633	total: 1m 5s	remaining: 35.7s
647:	learn: 0.8291292	total: 1m 5s	remaining: 35.6s
648:	learn: 0.8291057	total: 1m 5s	remaining: 35.5s
649:	learn: 0.8290700	total: 1m 5s	remaining: 35.4s
650:	learn: 0.8290420	total: 1m 5s	remaining: 35.3s
651:	learn: 0.8290116	total: 1m 5s	remaining: 35.2s
652:	learn: 0.8289841	total: 1m 6s	remaining: 35.1s
653:	learn: 0.8289796	total: 1m 6s	remaining: 35s
654:	learn: 0.8289486	total: 1m 6s	remaining: 34.9s
655:	learn: 0.82

...

267:	learn: 0.8397027	total: 27.8s	remaining: 1m 15s
268:	learn: 0.8396456	total: 27.9s	remaining: 1m 15s
269:	learn: 0.8396242	total: 28s	remaining: 1m 15s
270:	learn: 0.8395898	total: 28.1s	remaining: 1m 15s
271:	learn: 0.8395479	total: 28.2s	remaining: 1m 15s
272:	learn: 0.8395082	total: 28.3s	remaining: 1m 15s
273:	learn: 0.8395056	total: 28.4s	remaining: 1m 15s
274:	learn: 0.8394883	total: 28.5s	remaining: 1m 15s
275:	learn: 0.8394523	total: 28.6s	remaining: 1m 15s
276:	learn: 0.8394258	total: 28.7s	remaining: 1m 14s
277:	learn: 0.8393838	total: 28.8s	remaining: 1m 14s
278:	learn: 0.8393441	total: 28.9s	remaining: 1m 14s
279:	learn: 0.8393088	total: 29s	remaining: 1m 14s
280:	learn: 0.8392715	total: 29.2s	remaining: 1m 14s
281:	learn: 0.8392124	total: 29.3s	remaining: 1m 14s
282:	learn: 0.8391772	total: 29.4s	remaining: 1m 14s
283:	learn: 0.8391694	total: 29.5s	remaining: 1m 14s
284:	learn: 0.8391422	total: 29.6s	remaining: 1m 14s
285:	learn: 0.8391035	total: 29.7s	remaining: 1m 1

425:	learn: 0.8349782	total: 44s	remaining: 59.4s
426:	learn: 0.8349610	total: 44.1s	remaining: 59.2s
427:	learn: 0.8349433	total: 44.2s	remaining: 59.1s
428:	learn: 0.8349219	total: 44.3s	remaining: 59s
429:	learn: 0.8348933	total: 44.4s	remaining: 58.9s
430:	learn: 0.8348815	total: 44.5s	remaining: 58.8s
431:	learn: 0.8348619	total: 44.6s	remaining: 58.7s
432:	learn: 0.8348605	total: 44.7s	remaining: 58.6s
433:	learn: 0.8348217	total: 44.8s	remaining: 58.4s
434:	learn: 0.8347881	total: 44.9s	remaining: 58.4s
435:	learn: 0.8347776	total: 45s	remaining: 58.2s
436:	learn: 0.8347585	total: 45.1s	remaining: 58.1s
437:	learn: 0.8347489	total: 45.2s	remaining: 58s
438:	learn: 0.8347290	total: 45.3s	remaining: 57.9s
439:	learn: 0.8346868	total: 45.4s	remaining: 57.8s
440:	learn: 0.8346511	total: 45.5s	remaining: 57.7s
441:	learn: 0.8346136	total: 45.6s	remaining: 57.6s
442:	learn: 0.8345934	total: 45.7s	remaining: 57.5s
443:	learn: 0.8345736	total: 45.8s	remaining: 57.4s
444:	learn: 0.834543

585:	learn: 0.8310313	total: 1m	remaining: 42.5s
586:	learn: 0.8310121	total: 1m	remaining: 42.3s
587:	learn: 0.8309930	total: 1m	remaining: 42.2s
588:	learn: 0.8309592	total: 1m	remaining: 42.1s
589:	learn: 0.8309284	total: 1m	remaining: 42s
590:	learn: 0.8309094	total: 1m	remaining: 41.9s
591:	learn: 0.8308782	total: 1m	remaining: 41.8s
592:	learn: 0.8308435	total: 1m	remaining: 41.7s
593:	learn: 0.8308225	total: 1m	remaining: 41.6s
594:	learn: 0.8307956	total: 1m	remaining: 41.5s
595:	learn: 0.8307908	total: 1m 1s	remaining: 41.4s
596:	learn: 0.8307539	total: 1m 1s	remaining: 41.3s
597:	learn: 0.8307274	total: 1m 1s	remaining: 41.2s
598:	learn: 0.8307045	total: 1m 1s	remaining: 41.1s
599:	learn: 0.8306822	total: 1m 1s	remaining: 41s
600:	learn: 0.8306609	total: 1m 1s	remaining: 40.9s
601:	learn: 0.8306155	total: 1m 1s	remaining: 40.8s
602:	learn: 0.8306038	total: 1m 1s	remaining: 40.7s
603:	learn: 0.8305906	total: 1m 1s	remaining: 40.6s
604:	learn: 0.8305544	total: 1m 2s	remaining: 

743:	learn: 0.8275485	total: 1m 15s	remaining: 26.1s
744:	learn: 0.8275432	total: 1m 16s	remaining: 26s
745:	learn: 0.8275371	total: 1m 16s	remaining: 25.9s
746:	learn: 0.8275082	total: 1m 16s	remaining: 25.8s
747:	learn: 0.8274827	total: 1m 16s	remaining: 25.7s
748:	learn: 0.8274724	total: 1m 16s	remaining: 25.6s
749:	learn: 0.8274414	total: 1m 16s	remaining: 25.5s
750:	learn: 0.8274405	total: 1m 16s	remaining: 25.4s
751:	learn: 0.8274272	total: 1m 16s	remaining: 25.3s
752:	learn: 0.8273974	total: 1m 16s	remaining: 25.2s
753:	learn: 0.8273682	total: 1m 16s	remaining: 25.1s
754:	learn: 0.8273399	total: 1m 17s	remaining: 25s
755:	learn: 0.8273266	total: 1m 17s	remaining: 24.9s
756:	learn: 0.8272956	total: 1m 17s	remaining: 24.8s
757:	learn: 0.8272677	total: 1m 17s	remaining: 24.7s
758:	learn: 0.8272394	total: 1m 17s	remaining: 24.6s
759:	learn: 0.8272070	total: 1m 17s	remaining: 24.5s
760:	learn: 0.8272059	total: 1m 17s	remaining: 24.4s
761:	learn: 0.8271790	total: 1m 17s	remaining: 24.

900:	learn: 0.8240758	total: 1m 31s	remaining: 10.1s
901:	learn: 0.8240573	total: 1m 32s	remaining: 10s
902:	learn: 0.8240284	total: 1m 32s	remaining: 9.9s
903:	learn: 0.8240007	total: 1m 32s	remaining: 9.8s
904:	learn: 0.8239724	total: 1m 32s	remaining: 9.7s
905:	learn: 0.8239672	total: 1m 32s	remaining: 9.59s
906:	learn: 0.8239297	total: 1m 32s	remaining: 9.49s
907:	learn: 0.8239031	total: 1m 32s	remaining: 9.39s
908:	learn: 0.8238668	total: 1m 32s	remaining: 9.29s
909:	learn: 0.8238532	total: 1m 32s	remaining: 9.19s
910:	learn: 0.8238310	total: 1m 32s	remaining: 9.08s
911:	learn: 0.8238242	total: 1m 33s	remaining: 8.98s
912:	learn: 0.8237948	total: 1m 33s	remaining: 8.88s
913:	learn: 0.8237713	total: 1m 33s	remaining: 8.78s
914:	learn: 0.8237459	total: 1m 33s	remaining: 8.68s
915:	learn: 0.8237310	total: 1m 33s	remaining: 8.57s
916:	learn: 0.8237197	total: 1m 33s	remaining: 8.47s
917:	learn: 0.8236902	total: 1m 33s	remaining: 8.37s
918:	learn: 0.8236671	total: 1m 33s	remaining: 8.27

In [11]:
scores

{'fit_time': array([102.28253484, 102.06701207, 102.38217974, 101.63458133,
        103.07627583]),
 'score_time': array([0.09103394, 0.09189773, 0.0910964 , 0.09150481, 0.09127855]),
 'test_score': array([-0.84341781, -0.84537946, -0.84437322, -0.84320546, -0.84200925]),
 'train_score': array([-0.82170936, -0.82121502, -0.82161349, -0.82272889, -0.82258591])}

In [12]:
scores['test_score'].mean()

-0.8436770380536011

In [19]:
submission = submit(cbr)
submission.head()

Learning rate set to 0.107728
0:	learn: 0.8839277	total: 146ms	remaining: 2m 25s
1:	learn: 0.8811116	total: 256ms	remaining: 2m 7s
2:	learn: 0.8787238	total: 415ms	remaining: 2m 17s
3:	learn: 0.8767797	total: 564ms	remaining: 2m 20s
4:	learn: 0.8751148	total: 655ms	remaining: 2m 10s
5:	learn: 0.8734477	total: 770ms	remaining: 2m 7s
6:	learn: 0.8720372	total: 869ms	remaining: 2m 3s
7:	learn: 0.8706866	total: 1s	remaining: 2m 4s
8:	learn: 0.8695030	total: 1.12s	remaining: 2m 3s
9:	learn: 0.8683646	total: 1.21s	remaining: 1m 59s
10:	learn: 0.8674941	total: 1.33s	remaining: 2m
11:	learn: 0.8666516	total: 1.45s	remaining: 1m 59s
12:	learn: 0.8658779	total: 1.57s	remaining: 1m 59s
13:	learn: 0.8650691	total: 1.68s	remaining: 1m 58s
14:	learn: 0.8643753	total: 1.81s	remaining: 1m 58s
15:	learn: 0.8636825	total: 1.94s	remaining: 1m 59s
16:	learn: 0.8631119	total: 2.03s	remaining: 1m 57s
17:	learn: 0.8625835	total: 2.17s	remaining: 1m 58s
18:	learn: 0.8621285	total: 2.31s	remaining: 1m 59s
19:	

160:	learn: 0.8442475	total: 21s	remaining: 1m 49s
161:	learn: 0.8442011	total: 21.1s	remaining: 1m 49s
162:	learn: 0.8441479	total: 21.3s	remaining: 1m 49s
163:	learn: 0.8441207	total: 21.4s	remaining: 1m 48s
164:	learn: 0.8440734	total: 21.5s	remaining: 1m 48s
165:	learn: 0.8440173	total: 21.6s	remaining: 1m 48s
166:	learn: 0.8439455	total: 21.7s	remaining: 1m 48s
167:	learn: 0.8438895	total: 21.9s	remaining: 1m 48s
168:	learn: 0.8438367	total: 22s	remaining: 1m 48s
169:	learn: 0.8437890	total: 22.1s	remaining: 1m 48s
170:	learn: 0.8437568	total: 22.3s	remaining: 1m 48s
171:	learn: 0.8437068	total: 22.4s	remaining: 1m 47s
172:	learn: 0.8436633	total: 22.5s	remaining: 1m 47s
173:	learn: 0.8436110	total: 22.7s	remaining: 1m 47s
174:	learn: 0.8435467	total: 22.8s	remaining: 1m 47s
175:	learn: 0.8434949	total: 23s	remaining: 1m 47s
176:	learn: 0.8434372	total: 23.1s	remaining: 1m 47s
177:	learn: 0.8433798	total: 23.2s	remaining: 1m 47s
178:	learn: 0.8433383	total: 23.4s	remaining: 1m 47s

316:	learn: 0.8386828	total: 41.6s	remaining: 1m 29s
317:	learn: 0.8386657	total: 41.7s	remaining: 1m 29s
318:	learn: 0.8386605	total: 41.8s	remaining: 1m 29s
319:	learn: 0.8386280	total: 41.9s	remaining: 1m 29s
320:	learn: 0.8385909	total: 42.1s	remaining: 1m 28s
321:	learn: 0.8385614	total: 42.2s	remaining: 1m 28s
322:	learn: 0.8385219	total: 42.3s	remaining: 1m 28s
323:	learn: 0.8384843	total: 42.5s	remaining: 1m 28s
324:	learn: 0.8384515	total: 42.6s	remaining: 1m 28s
325:	learn: 0.8384184	total: 42.7s	remaining: 1m 28s
326:	learn: 0.8383737	total: 42.9s	remaining: 1m 28s
327:	learn: 0.8383699	total: 43s	remaining: 1m 28s
328:	learn: 0.8383618	total: 43.1s	remaining: 1m 27s
329:	learn: 0.8383336	total: 43.3s	remaining: 1m 27s
330:	learn: 0.8382983	total: 43.4s	remaining: 1m 27s
331:	learn: 0.8382750	total: 43.5s	remaining: 1m 27s
332:	learn: 0.8382379	total: 43.6s	remaining: 1m 27s
333:	learn: 0.8382164	total: 43.8s	remaining: 1m 27s
334:	learn: 0.8381779	total: 43.9s	remaining: 1m

472:	learn: 0.8349603	total: 1m 1s	remaining: 1m 8s
473:	learn: 0.8349264	total: 1m 1s	remaining: 1m 8s
474:	learn: 0.8348977	total: 1m 2s	remaining: 1m 8s
475:	learn: 0.8348826	total: 1m 2s	remaining: 1m 8s
476:	learn: 0.8348773	total: 1m 2s	remaining: 1m 8s
477:	learn: 0.8348532	total: 1m 2s	remaining: 1m 8s
478:	learn: 0.8348367	total: 1m 2s	remaining: 1m 7s
479:	learn: 0.8348159	total: 1m 2s	remaining: 1m 7s
480:	learn: 0.8348023	total: 1m 2s	remaining: 1m 7s
481:	learn: 0.8347808	total: 1m 2s	remaining: 1m 7s
482:	learn: 0.8347587	total: 1m 3s	remaining: 1m 7s
483:	learn: 0.8347293	total: 1m 3s	remaining: 1m 7s
484:	learn: 0.8347029	total: 1m 3s	remaining: 1m 7s
485:	learn: 0.8346878	total: 1m 3s	remaining: 1m 7s
486:	learn: 0.8346712	total: 1m 3s	remaining: 1m 6s
487:	learn: 0.8346701	total: 1m 3s	remaining: 1m 6s
488:	learn: 0.8346428	total: 1m 3s	remaining: 1m 6s
489:	learn: 0.8346179	total: 1m 3s	remaining: 1m 6s
490:	learn: 0.8345880	total: 1m 4s	remaining: 1m 6s
491:	learn: 

629:	learn: 0.8318045	total: 1m 22s	remaining: 48.2s
630:	learn: 0.8317741	total: 1m 22s	remaining: 48.1s
631:	learn: 0.8317516	total: 1m 22s	remaining: 47.9s
632:	learn: 0.8317212	total: 1m 22s	remaining: 47.8s
633:	learn: 0.8316954	total: 1m 22s	remaining: 47.7s
634:	learn: 0.8316805	total: 1m 22s	remaining: 47.5s
635:	learn: 0.8316634	total: 1m 22s	remaining: 47.4s
636:	learn: 0.8316437	total: 1m 22s	remaining: 47.3s
637:	learn: 0.8316304	total: 1m 23s	remaining: 47.1s
638:	learn: 0.8316011	total: 1m 23s	remaining: 47s
639:	learn: 0.8315837	total: 1m 23s	remaining: 46.9s
640:	learn: 0.8315701	total: 1m 23s	remaining: 46.7s
641:	learn: 0.8315451	total: 1m 23s	remaining: 46.6s
642:	learn: 0.8315172	total: 1m 23s	remaining: 46.5s
643:	learn: 0.8314998	total: 1m 23s	remaining: 46.3s
644:	learn: 0.8314767	total: 1m 23s	remaining: 46.2s
645:	learn: 0.8314731	total: 1m 24s	remaining: 46.1s
646:	learn: 0.8314456	total: 1m 24s	remaining: 45.9s
647:	learn: 0.8314415	total: 1m 24s	remaining: 4

785:	learn: 0.8286228	total: 1m 42s	remaining: 27.8s
786:	learn: 0.8286059	total: 1m 42s	remaining: 27.7s
787:	learn: 0.8285916	total: 1m 42s	remaining: 27.5s
788:	learn: 0.8285720	total: 1m 42s	remaining: 27.4s
789:	learn: 0.8285652	total: 1m 42s	remaining: 27.3s
790:	learn: 0.8285397	total: 1m 42s	remaining: 27.2s
791:	learn: 0.8285133	total: 1m 42s	remaining: 27s
792:	learn: 0.8285068	total: 1m 43s	remaining: 26.9s
793:	learn: 0.8284866	total: 1m 43s	remaining: 26.8s
794:	learn: 0.8284752	total: 1m 43s	remaining: 26.6s
795:	learn: 0.8284679	total: 1m 43s	remaining: 26.5s
796:	learn: 0.8284576	total: 1m 43s	remaining: 26.4s
797:	learn: 0.8284338	total: 1m 43s	remaining: 26.2s
798:	learn: 0.8284178	total: 1m 43s	remaining: 26.1s
799:	learn: 0.8283935	total: 1m 43s	remaining: 26s
800:	learn: 0.8283774	total: 1m 44s	remaining: 25.9s
801:	learn: 0.8283563	total: 1m 44s	remaining: 25.7s
802:	learn: 0.8283292	total: 1m 44s	remaining: 25.6s
803:	learn: 0.8283205	total: 1m 44s	remaining: 25.

942:	learn: 0.8257971	total: 2m 2s	remaining: 7.41s
943:	learn: 0.8257852	total: 2m 2s	remaining: 7.28s
944:	learn: 0.8257674	total: 2m 2s	remaining: 7.15s
945:	learn: 0.8257450	total: 2m 2s	remaining: 7.02s
946:	learn: 0.8257196	total: 2m 3s	remaining: 6.89s
947:	learn: 0.8256909	total: 2m 3s	remaining: 6.76s
948:	learn: 0.8256638	total: 2m 3s	remaining: 6.63s
949:	learn: 0.8256421	total: 2m 3s	remaining: 6.5s
950:	learn: 0.8256210	total: 2m 3s	remaining: 6.37s
951:	learn: 0.8255996	total: 2m 3s	remaining: 6.24s
952:	learn: 0.8255935	total: 2m 3s	remaining: 6.11s
953:	learn: 0.8255719	total: 2m 3s	remaining: 5.98s
954:	learn: 0.8255492	total: 2m 4s	remaining: 5.85s
955:	learn: 0.8255417	total: 2m 4s	remaining: 5.72s
956:	learn: 0.8255139	total: 2m 4s	remaining: 5.59s
957:	learn: 0.8254964	total: 2m 4s	remaining: 5.46s
958:	learn: 0.8254678	total: 2m 4s	remaining: 5.33s
959:	learn: 0.8254368	total: 2m 4s	remaining: 5.2s
960:	learn: 0.8254272	total: 2m 4s	remaining: 5.07s
961:	learn: 0.

id    target
0   0  7.710960
1   5  7.732050
2  15  7.729660
3  16  7.527546
4  17  7.285527

In [20]:
submission.to_csv('submission_catboost_default.csv', index=False)

# Train a random forest

In [53]:
x_train_oh = pd.get_dummies(x_train)
test_oh = pd.get_dummies(test)

In [54]:
test_oh.shape

(200000, 70)

In [55]:
x_train_oh.shape

(300000, 70)

In [56]:
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor(n_estimators=600, n_jobs=-2, random_state=42, min_samples_leaf=0.0001, verbose=1)

In [57]:
scores = cross_validate(rf, X=x_train_oh, y=y_train, cv=5, return_train_score = True,
                         scoring='neg_root_mean_squared_error', verbose=1)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=-2)]: Using backend LokyBackend with 7 concurrent workers.
[Parallel(n_jobs=-2)]: Done  36 tasks      | elapsed:   50.2s
[Parallel(n_jobs=-2)]: Done 186 tasks      | elapsed:  3.9min
[Parallel(n_jobs=-2)]: Done 436 tasks      | elapsed:  9.0min
[Parallel(n_jobs=-2)]: Done 600 out of 600 | elapsed: 12.2min finished
[Parallel(n_jobs=7)]: Using backend ThreadingBackend with 7 concurrent workers.
[Parallel(n_jobs=7)]: Done  36 tasks      | elapsed:    0.1s
[Parallel(n_jobs=7)]: Done 186 tasks      | elapsed:    0.4s
[Parallel(n_jobs=7)]: Done 436 tasks      | elapsed:    0.8s
[Parallel(n_jobs=7)]: Done 600 out of 600 | elapsed:    1.1s finished
[Parallel(n_jobs=7)]: Using backend ThreadingBackend with 7 concurrent workers.
[Parallel(n_jobs=7)]: Done  36 tasks      | elapsed:    0.3s
[Parallel(n_jobs=7)]: Done 186 tasks      | elapsed:    1.4s
[Parallel(n_jobs=7)]: Done 436 tasks      | elapsed

In [58]:
scores

{'fit_time': array([735.32043934, 736.87023497, 746.3355546 , 737.5243113 ,
        741.24415064]),
 'score_time': array([1.15778542, 1.10660458, 1.13768029, 1.13884997, 1.13567924]),
 'test_score': array([-0.85180736, -0.85246847, -0.85403798, -0.85382717, -0.85278999]),
 'train_score': array([-0.74666176, -0.74648601, -0.74611985, -0.74625115, -0.74675153])}

In [59]:
scores['test_score'].mean()

-0.8529861930591363

# Lightgbm parameter optimization

In [96]:
from lightgbm.sklearn import LGBMRegressor
from sklearn.model_selection import RandomizedSearchCV

In [97]:
from scipy.stats import uniform
from scipy.stats import expon
from sklearn.utils.fixes import loguniform

In [98]:
params = {'n_estimators':[10, 20, 50, 100, 200, 500, 1000, 2000],
          'reg_lambda':[0, 0.01, 0.1, 0.2, 0.4],
          'feature_fraction':[0.9, 0.8, 0.7, 0.6],
          'num_leaves':[5, 10, 31, 50, 100, 200]}

In [99]:
lgb = LGBMRegressor(n_jobs=-2, verbose=1)

In [100]:
cv = RandomizedSearchCV(lgb, params, return_train_score=True, verbose=100, 
                        scoring='neg_root_mean_squared_error', n_iter=300)

In [101]:
cv.fit(x_train, y_train)

Fitting 5 folds for each of 300 candidates, totalling 1500 fits
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[CV] reg_lambda=0.1, num_leaves=10, n_estimators=2000, feature_fraction=0.8 
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013783 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3629
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.456400
[CV]  reg_lambda=0.1, num_leaves=10, n_estimators=2000, feature_fraction=0.8, score=(train=-0.803, test=-0.845), total=   8.2s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   10

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014307 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.454541
[CV]  reg_lambda=0.1, num_leaves=200, n_estimators=1000, feature_fraction=0.9, score=(train=-0.500, test=-0.858), total=  11.2s
[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:  2.0min remaining:    0.0s
[CV] reg_lambda=0, num_leaves=31, n_estimators=500, feature_fraction=0.6 
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6


[CV]  reg_lambda=0.1, num_leaves=10, n_estimators=50, feature_fraction=0.8, score=(train=-0.853, test=-0.854), total=   0.6s
[Parallel(n_jobs=1)]: Done  19 out of  19 | elapsed:  2.4min remaining:    0.0s
[CV] reg_lambda=0.1, num_leaves=10, n_estimators=50, feature_fraction=0.8 
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013904 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.454541
[CV]  reg_lambda=0.1, num_leaves=10, n_estimators=50, feature_fraction=0.8, score=(train=-0.854, test=-0.854), total=   0.6s
[

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014115 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.456370
[CV]  reg_lambda=0.01, num_leaves=200, n_estimators=200, feature_fraction=0.6, score=(train=-0.750, test=-0.848), total=   2.8s
[Parallel(n_jobs=1)]: Done  29 out of  29 | elapsed:  2.8min remaining:    0.0s
[CV] reg_lambda=0.01, num_leaves=200, n_estimators=200, feature_fraction=0.6 
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=

[CV]  reg_lambda=0.2, num_leaves=5, n_estimators=100, feature_fraction=0.9, score=(train=-0.852, test=-0.854), total=   0.8s
[Parallel(n_jobs=1)]: Done  38 out of  38 | elapsed:  3.1min remaining:    0.0s
[CV] reg_lambda=0.2, num_leaves=5, n_estimators=100, feature_fraction=0.9 
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014217 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.456370
[CV]  reg_lambda=0.2, num_leaves=5, n_estimators=100, feature_fraction=0.9, score=(train=-0.852, test=-0.853), total=   0.8s
[

...

[CV]  reg_lambda=0.01, num_leaves=31, n_estimators=10, feature_fraction=0.9, score=(train=-0.865, test=-0.867), total=   0.4s
[CV] reg_lambda=0.01, num_leaves=31, n_estimators=10, feature_fraction=0.9 
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014304 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.456370
[CV]  reg_lambda=0.01, num_leaves=31, n_estimators=10, feature_fraction=0.9, score=(train=-0.866, test=-0.866), total=   0.4s
[CV] reg_lambda=0.01, num_leaves=31, n_estimators=10, feature_fraction=0.9 
[L

[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014263 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.456370
[CV]  reg_lambda=0, num_leaves=100, n_estimators=1000, feature_fraction=0.7, score=(train=-0.648, test=-0.852), total=   7.4s
[CV] reg_lambda=0, num_leaves=100, n_estimators=1000, feature_fraction=0.7 
[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of tes

[CV]  reg_lambda=0.2, num_leaves=200, n_estimators=20, feature_fraction=0.6, score=(train=-0.842, test=-0.853), total=   0.6s
[CV] reg_lambda=0.2, num_leaves=200, n_estimators=20, feature_fraction=0.6 
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013943 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.454541
[CV]  reg_lambda=0.2, num_leaves=200, n_estimators=20, feature_fraction=0.6, score=(train=-0.843, test=-0.853), total=   0.6s
[CV] reg_lambda=0, num_leaves=5, n_estimators=500, feature_fraction=0.7 
[Ligh

[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013756 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3630
[LightGBM] [Info] Number of data points in the train set: 240000, number of used features: 24
[LightGBM] [Info] Start training from score 7.454541
[CV]  reg_lambda=0, num_leaves=31, n_estimators=500, feature_fraction=0.7, score=(train=-0.806, test=-0.844), total=   3.0s
[CV] reg_lambda=0.01, num_leaves=31, n_estimators=1000, feature_fraction=0.8 
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of tes

RandomizedSearchCV(estimator=LGBMRegressor(n_jobs=-2, verbose=1), n_iter=300,
                   param_distributions={'feature_fraction': [0.9, 0.8, 0.7,
                                                             0.6],
                                        'n_estimators': [10, 20, 50, 100, 200,
                                                         500, 1000, 2000],
                                        'num_leaves': [5, 10, 31, 50, 100, 200],
                                        'reg_lambda': [0, 0.01, 0.1, 0.2, 0.4]},
                   return_train_score=True,
                   scoring='neg_root_mean_squared_error', verbose=100)

In [102]:
cv.best_params_

{'reg_lambda': 0.1,
 'num_leaves': 5,
 'n_estimators': 2000,
 'feature_fraction': 0.7}

In [103]:
cv.best_score_

-0.843655856198037

In [104]:
cv.cv_results_

{'mean_fit_time': array([ 7.356423  , 10.47312803,  2.66133189,  0.55567026,  0.74290981,
         2.53206463,  1.88655486,  0.71852727,  1.1210885 ,  1.58682647,
         0.93445697, 18.36201053,  1.01247835, 18.34217839,  4.01014757,
         0.61392269,  1.17339091,  1.5472878 ,  0.62434478,  0.41445537,
         0.67769508,  1.60498333,  2.23799415,  0.47407074,  6.87294922,
         0.38252597,  1.10567613,  2.26627531,  1.36020012,  1.87365942,
         4.00318103,  3.19579706,  1.01745257,  0.4000226 ,  1.24584737,
        18.50552983,  8.36161485,  0.81561275,  0.37185431,  2.83799934,
         2.96497946,  1.27942734,  0.636903  ,  0.3348897 ,  0.33065653,
         0.39925866,  8.00710626,  3.05481644,  1.68161087, 19.78848443,
         0.81278005,  1.19120593, 19.48993683,  3.8974823 ,  1.06353984,
         0.35452132,  4.52773366,  3.73884664,  0.81057835,  0.38210797,
         6.52083902,  0.53322005,  5.29409847,  6.73513041,  0.428579  ,
         9.82113161, 10.6659265 , 

# Catboost parameter optimization

In [9]:
from catboost import CatBoostRegressor
from sklearn.model_selection import RandomizedSearchCV

In [10]:
cbr = CatBoostRegressor(thread_count=6)

In [11]:
params = {
    'iterations':[200, 500, 1000, 2000],
    'depth':[6, 8, 10],
    'l2_leaf_reg':[1,3,6,12]
}

In [12]:
cv = RandomizedSearchCV(cbr, params, return_train_score=True, verbose=100, 
                       scoring='neg_root_mean_squared_error', n_iter=25)

In [ ]:
cv.fit(x_train, y_train)

Fitting 5 folds for each of 25 candidates, totalling 125 fits
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[CV] l2_leaf_reg=6, iterations=500, depth=6 ..........................
0:	learn: 0.8860192	total: 198ms	remaining: 1m 38s
1:	learn: 0.8851159	total: 288ms	remaining: 1m 11s
2:	learn: 0.8842548	total: 428ms	remaining: 1m 10s
3:	learn: 0.8834351	total: 540ms	remaining: 1m 6s
4:	learn: 0.8826614	total: 613ms	remaining: 1m
5:	learn: 0.8819479	total: 686ms	remaining: 56.5s
6:	learn: 0.8812081	total: 776ms	remaining: 54.7s
7:	learn: 0.8805594	total: 851ms	remaining: 52.3s
8:	learn: 0.8799360	total: 926ms	remaining: 50.5s
9:	learn: 0.8792961	total: 1.01s	remaining: 49.7s
10:	learn: 0.8786720	total: 1.09s	remaining: 48.5s
11:	learn: 0.8780930	total: 1.18s	remaining: 48s
12:	learn: 0.8775315	total: 1.25s	remaining: 46.8s
13:	learn: 0.8770059	total: 1.31s	remaining: 45.5s
14:	learn: 0.8764673	total: 1.39s	remaining: 44.9s
15:	learn: 0.8759631	total: 1.47s

158:	learn: 0.8545538	total: 15s	remaining: 32.3s
159:	learn: 0.8545073	total: 15.2s	remaining: 32.2s
160:	learn: 0.8544669	total: 15.3s	remaining: 32.1s
161:	learn: 0.8544149	total: 15.4s	remaining: 32.1s
162:	learn: 0.8543695	total: 15.5s	remaining: 32s
163:	learn: 0.8543141	total: 15.6s	remaining: 31.9s
164:	learn: 0.8542577	total: 15.7s	remaining: 31.8s
165:	learn: 0.8542107	total: 15.8s	remaining: 31.8s
166:	learn: 0.8541588	total: 15.9s	remaining: 31.7s
167:	learn: 0.8541206	total: 16s	remaining: 31.6s
168:	learn: 0.8540742	total: 16.1s	remaining: 31.5s
169:	learn: 0.8540366	total: 16.2s	remaining: 31.4s
170:	learn: 0.8539963	total: 16.3s	remaining: 31.4s
171:	learn: 0.8539513	total: 16.4s	remaining: 31.3s
172:	learn: 0.8539017	total: 16.5s	remaining: 31.2s
173:	learn: 0.8538524	total: 16.6s	remaining: 31.1s
174:	learn: 0.8538091	total: 16.7s	remaining: 31.1s
175:	learn: 0.8537494	total: 16.8s	remaining: 31s
176:	learn: 0.8536978	total: 16.9s	remaining: 30.9s
177:	learn: 0.853652

318:	learn: 0.8492153	total: 31.5s	remaining: 17.9s
319:	learn: 0.8491934	total: 31.6s	remaining: 17.8s
320:	learn: 0.8491619	total: 31.7s	remaining: 17.7s
321:	learn: 0.8491464	total: 31.8s	remaining: 17.6s
322:	learn: 0.8491263	total: 31.9s	remaining: 17.5s
323:	learn: 0.8491083	total: 32s	remaining: 17.4s
324:	learn: 0.8490731	total: 32.1s	remaining: 17.3s
325:	learn: 0.8490554	total: 32.2s	remaining: 17.2s
326:	learn: 0.8490280	total: 32.3s	remaining: 17.1s
327:	learn: 0.8490092	total: 32.4s	remaining: 17s
328:	learn: 0.8489855	total: 32.5s	remaining: 16.9s
329:	learn: 0.8489561	total: 32.6s	remaining: 16.8s
330:	learn: 0.8489364	total: 32.7s	remaining: 16.7s
331:	learn: 0.8489134	total: 32.8s	remaining: 16.6s
332:	learn: 0.8488947	total: 32.9s	remaining: 16.5s
333:	learn: 0.8488677	total: 33s	remaining: 16.4s
334:	learn: 0.8488406	total: 33.1s	remaining: 16.3s
335:	learn: 0.8488235	total: 33.2s	remaining: 16.2s
336:	learn: 0.8488001	total: 33.3s	remaining: 16.1s
337:	learn: 0.8487

479:	learn: 0.8457690	total: 48.3s	remaining: 2.01s
480:	learn: 0.8457476	total: 48.4s	remaining: 1.91s
481:	learn: 0.8457289	total: 48.5s	remaining: 1.81s
482:	learn: 0.8457170	total: 48.6s	remaining: 1.71s
483:	learn: 0.8456942	total: 48.7s	remaining: 1.61s
484:	learn: 0.8456745	total: 48.8s	remaining: 1.51s
485:	learn: 0.8456522	total: 48.9s	remaining: 1.41s
486:	learn: 0.8456328	total: 49s	remaining: 1.31s
487:	learn: 0.8456202	total: 49.1s	remaining: 1.21s
488:	learn: 0.8455969	total: 49.2s	remaining: 1.11s
489:	learn: 0.8455775	total: 49.3s	remaining: 1.01s
490:	learn: 0.8455562	total: 49.4s	remaining: 906ms
491:	learn: 0.8455301	total: 49.6s	remaining: 806ms
492:	learn: 0.8455090	total: 49.7s	remaining: 705ms
493:	learn: 0.8454870	total: 49.8s	remaining: 605ms
494:	learn: 0.8454705	total: 49.9s	remaining: 504ms
495:	learn: 0.8454516	total: 50s	remaining: 403ms
496:	learn: 0.8454305	total: 50.1s	remaining: 302ms
497:	learn: 0.8454139	total: 50.2s	remaining: 202ms
498:	learn: 0.84

135:	learn: 0.8553381	total: 13s	remaining: 34.7s
136:	learn: 0.8552635	total: 13.1s	remaining: 34.6s
137:	learn: 0.8552096	total: 13.1s	remaining: 34.5s
138:	learn: 0.8551466	total: 13.2s	remaining: 34.4s
139:	learn: 0.8550973	total: 13.4s	remaining: 34.3s
140:	learn: 0.8550287	total: 13.5s	remaining: 34.3s
141:	learn: 0.8549696	total: 13.6s	remaining: 34.2s
142:	learn: 0.8549083	total: 13.7s	remaining: 34.1s
143:	learn: 0.8548446	total: 13.8s	remaining: 34s
144:	learn: 0.8547794	total: 13.8s	remaining: 33.9s
145:	learn: 0.8547187	total: 13.9s	remaining: 33.8s
146:	learn: 0.8546517	total: 14s	remaining: 33.7s
147:	learn: 0.8546083	total: 14.1s	remaining: 33.6s
148:	learn: 0.8545581	total: 14.2s	remaining: 33.5s
149:	learn: 0.8544983	total: 14.3s	remaining: 33.5s
150:	learn: 0.8544482	total: 14.4s	remaining: 33.4s
151:	learn: 0.8543898	total: 14.6s	remaining: 33.3s
152:	learn: 0.8543383	total: 14.7s	remaining: 33.3s
153:	learn: 0.8542849	total: 14.8s	remaining: 33.2s
154:	learn: 0.8542

...

414:	learn: 0.8339019	total: 1m 28s	remaining: 2m 5s
415:	learn: 0.8338577	total: 1m 29s	remaining: 2m 5s
416:	learn: 0.8338106	total: 1m 29s	remaining: 2m 4s
417:	learn: 0.8337817	total: 1m 29s	remaining: 2m 4s
418:	learn: 0.8337435	total: 1m 29s	remaining: 2m 4s
419:	learn: 0.8337093	total: 1m 30s	remaining: 2m 4s
420:	learn: 0.8336498	total: 1m 30s	remaining: 2m 4s
421:	learn: 0.8336024	total: 1m 30s	remaining: 2m 3s
422:	learn: 0.8335627	total: 1m 30s	remaining: 2m 3s
423:	learn: 0.8335206	total: 1m 30s	remaining: 2m 3s
424:	learn: 0.8334756	total: 1m 31s	remaining: 2m 3s
425:	learn: 0.8334029	total: 1m 31s	remaining: 2m 3s
426:	learn: 0.8333447	total: 1m 31s	remaining: 2m 2s
427:	learn: 0.8333049	total: 1m 31s	remaining: 2m 2s
428:	learn: 0.8332775	total: 1m 32s	remaining: 2m 2s
429:	learn: 0.8332137	total: 1m 32s	remaining: 2m 2s
430:	learn: 0.8331691	total: 1m 32s	remaining: 2m 2s
431:	learn: 0.8331233	total: 1m 32s	remaining: 2m 1s
432:	learn: 0.8330529	total: 1m 33s	remaining:

567:	learn: 0.8270972	total: 2m 2s	remaining: 1m 33s
568:	learn: 0.8270615	total: 2m 3s	remaining: 1m 33s
569:	learn: 0.8270155	total: 2m 3s	remaining: 1m 33s
570:	learn: 0.8269976	total: 2m 3s	remaining: 1m 32s
571:	learn: 0.8269440	total: 2m 3s	remaining: 1m 32s
572:	learn: 0.8269045	total: 2m 4s	remaining: 1m 32s
573:	learn: 0.8268595	total: 2m 4s	remaining: 1m 32s
574:	learn: 0.8268065	total: 2m 4s	remaining: 1m 32s
575:	learn: 0.8267688	total: 2m 4s	remaining: 1m 31s
576:	learn: 0.8267276	total: 2m 4s	remaining: 1m 31s
577:	learn: 0.8266797	total: 2m 5s	remaining: 1m 31s
578:	learn: 0.8266497	total: 2m 5s	remaining: 1m 31s
579:	learn: 0.8266059	total: 2m 5s	remaining: 1m 31s
580:	learn: 0.8265706	total: 2m 5s	remaining: 1m 30s
581:	learn: 0.8265440	total: 2m 6s	remaining: 1m 30s
582:	learn: 0.8264735	total: 2m 6s	remaining: 1m 30s
583:	learn: 0.8264387	total: 2m 6s	remaining: 1m 30s
584:	learn: 0.8264067	total: 2m 6s	remaining: 1m 29s
585:	learn: 0.8263554	total: 2m 7s	remaining: 

721:	learn: 0.8206747	total: 2m 37s	remaining: 1m
722:	learn: 0.8206481	total: 2m 37s	remaining: 1m
723:	learn: 0.8205926	total: 2m 38s	remaining: 1m
724:	learn: 0.8205541	total: 2m 38s	remaining: 1m
725:	learn: 0.8204937	total: 2m 38s	remaining: 59.9s
726:	learn: 0.8204710	total: 2m 38s	remaining: 59.7s
727:	learn: 0.8204139	total: 2m 39s	remaining: 59.4s
728:	learn: 0.8203657	total: 2m 39s	remaining: 59.2s
729:	learn: 0.8203263	total: 2m 39s	remaining: 59s
730:	learn: 0.8202899	total: 2m 39s	remaining: 58.8s
731:	learn: 0.8202428	total: 2m 39s	remaining: 58.6s
732:	learn: 0.8202132	total: 2m 40s	remaining: 58.3s
733:	learn: 0.8201765	total: 2m 40s	remaining: 58.1s
734:	learn: 0.8201530	total: 2m 40s	remaining: 57.9s
735:	learn: 0.8201018	total: 2m 40s	remaining: 57.7s
736:	learn: 0.8200830	total: 2m 41s	remaining: 57.5s
737:	learn: 0.8200428	total: 2m 41s	remaining: 57.3s
738:	learn: 0.8200133	total: 2m 41s	remaining: 57.1s
739:	learn: 0.8199562	total: 2m 41s	remaining: 56.8s
740:	le

878:	learn: 0.8153229	total: 3m 12s	remaining: 26.5s
879:	learn: 0.8153096	total: 3m 12s	remaining: 26.3s
880:	learn: 0.8152865	total: 3m 13s	remaining: 26.1s
881:	learn: 0.8152675	total: 3m 13s	remaining: 25.9s
882:	learn: 0.8152216	total: 3m 13s	remaining: 25.7s
883:	learn: 0.8151689	total: 3m 13s	remaining: 25.4s
884:	learn: 0.8151519	total: 3m 14s	remaining: 25.2s
885:	learn: 0.8151127	total: 3m 14s	remaining: 25s
886:	learn: 0.8150585	total: 3m 14s	remaining: 24.8s
887:	learn: 0.8150344	total: 3m 14s	remaining: 24.6s
888:	learn: 0.8149824	total: 3m 15s	remaining: 24.4s
889:	learn: 0.8149821	total: 3m 15s	remaining: 24.1s
890:	learn: 0.8149392	total: 3m 15s	remaining: 23.9s
891:	learn: 0.8148912	total: 3m 15s	remaining: 23.7s
892:	learn: 0.8148686	total: 3m 16s	remaining: 23.5s
893:	learn: 0.8148368	total: 3m 16s	remaining: 23.3s
894:	learn: 0.8148086	total: 3m 16s	remaining: 23.1s
895:	learn: 0.8147763	total: 3m 16s	remaining: 22.8s
896:	learn: 0.8147540	total: 3m 16s	remaining: 2

30:	learn: 0.8648371	total: 6.25s	remaining: 3m 15s
31:	learn: 0.8644580	total: 6.46s	remaining: 3m 15s
32:	learn: 0.8640915	total: 6.66s	remaining: 3m 15s
33:	learn: 0.8637325	total: 6.87s	remaining: 3m 15s
34:	learn: 0.8633976	total: 7.09s	remaining: 3m 15s
35:	learn: 0.8630644	total: 7.32s	remaining: 3m 16s
36:	learn: 0.8627645	total: 7.51s	remaining: 3m 15s
37:	learn: 0.8624385	total: 7.74s	remaining: 3m 16s
38:	learn: 0.8621272	total: 7.93s	remaining: 3m 15s
39:	learn: 0.8618447	total: 8.16s	remaining: 3m 15s
40:	learn: 0.8615712	total: 8.35s	remaining: 3m 15s
41:	learn: 0.8612792	total: 8.59s	remaining: 3m 15s
42:	learn: 0.8609887	total: 8.84s	remaining: 3m 16s
43:	learn: 0.8606938	total: 9.09s	remaining: 3m 17s
44:	learn: 0.8604090	total: 9.32s	remaining: 3m 17s
45:	learn: 0.8601529	total: 9.54s	remaining: 3m 17s
46:	learn: 0.8598937	total: 9.76s	remaining: 3m 17s
47:	learn: 0.8596477	total: 9.99s	remaining: 3m 18s
48:	learn: 0.8594329	total: 10.2s	remaining: 3m 18s
49:	learn: 0

In [ ]:
cv.best_score_

In [ ]:
cv.best_params_

# XGBoost default

In [8]:
from xgboost import XGBRegressor

In [9]:
xgb = XGBRegressor(n_jobs=-2)
from categorical_transform import OneHotTransform
from sklearn.pipeline import Pipeline
xgb_pipe = Pipeline([('one hot encode',OneHotTransform()),('xgboost', xgb)])

In [11]:
scores = cross_validate(xgb_pipe, X=x_train, y=y_train, cv=5, return_train_score = True,
                         scoring='neg_root_mean_squared_error')

In [12]:
scores

{'fit_time': array([24.12835169, 24.08186555, 24.08900762, 24.60427237, 24.29017138]),
 'score_time': array([0.09085464, 0.09464645, 0.09508634, 0.09631681, 0.09489894]),
 'test_score': array([-0.84899968, -0.85142876, -0.84975748, -0.84827894, -0.8475177 ]),
 'train_score': array([-0.80958961, -0.81035048, -0.8102819 , -0.81008866, -0.80988856])}

In [13]:
scores['test_score'].mean()

-0.8491965127087816

# Stacking

In [8]:
from sklearn.ensemble import StackingRegressor
from xgboost import XGBRegressor
from lightgbm.sklearn import LGBMRegressor
from catboost import CatBoostRegressor

In [9]:
xgb = XGBRegressor(n_jobs=-2)
from categorical_transform import OneHotTransform
from sklearn.pipeline import Pipeline
xgb_pipe = Pipeline([('one hot encode',OneHotTransform()),('xgboost', xgb)])

In [10]:
reg = StackingRegressor(estimators = [('lgbm', LGBMRegressor()), 
                                      ('catboost', CatBoostRegressor(cat_features=cat_cols)),
                                      ('xgboost', xgb_pipe)
                                      ], verbose=1)

In [11]:
scores = cross_validate(reg, X=x_train, y=y_train, cv=5, return_train_score = True,
                         scoring='neg_root_mean_squared_error', verbose=100, n_jobs=-2)

[Parallel(n_jobs=-2)]: Using backend LokyBackend with 7 concurrent workers.
[Parallel(n_jobs=-2)]: Done   1 tasks      | elapsed: 63.6min
[Parallel(n_jobs=-2)]: Done   2 out of   5 | elapsed: 63.6min remaining: 95.4min
[Parallel(n_jobs=-2)]: Done   3 out of   5 | elapsed: 63.6min remaining: 42.4min
[Parallel(n_jobs=-2)]: Done   5 out of   5 | elapsed: 63.7min remaining:    0.0s
[Parallel(n_jobs=-2)]: Done   5 out of   5 | elapsed: 63.7min finished


In [12]:
scores

{'fit_time': array([3815.40454006, 3807.97124004, 3811.49092984, 3807.93640614,
        3805.41960287]),
 'score_time': array([1.09986401, 1.87512612, 1.90971828, 1.91814828, 2.42548656]),
 'test_score': array([-0.84303774, -0.84522483, -0.84403687, -0.84280014, -0.8418344 ]),
 'train_score': array([-0.8216549 , -0.82103128, -0.82241718, -0.82290083, -0.82262285])}

In [13]:
scores['test_score'].mean()

-0.8433867948626164